<a href="https://colab.research.google.com/github/wiatrak2/BScThesis/blob/master/conceptors3D.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive')
import sys
sys.path.append('BScThesis/')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [2]:
!pip3 install torch torchvision


    100% |████████████████████████████████| 519.5MB 29kB/s 
tcmalloc: large alloc 1073750016 bytes == 0x58c46000 @  0x7f9ec807e2a4 0x591a07 0x5b5d56 0x502e9a 0x506859 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x504c28 0x502540 0x502f3d 0x507641
    100% |████████████████████████████████| 61kB 17.0MB/s 
    100% |████████████████████████████████| 2.0MB 5.0MB/s 
  Found existing installation: Pillow 4.0.0
    Uninstalling Pillow-4.0.0:
      Successfully uninstalled Pillow-4.0.0


In [3]:
!git clone https://github.com/wiatrak2/BScThesis

Cloning into 'BScThesis'...
remote: Enumerating objects: 83, done.
remote: Counting objects: 100% (83/83), done.
remote: Compressing objects: 100% (67/67), done.
remote: Total 262 (delta 43), reused 41 (delta 16), pack-reused 179
Receiving objects: 100% (262/262), 20.32 MiB | 8.98 MiB/s, done.
Resolving deltas: 100% (142/142), done.


In [0]:
from importlib import reload 

In [0]:
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

In [0]:
import torchvision
import torchvision.transforms as transforms

In [0]:
import matplotlib.pyplot as plt
import pickle
import sympy
from collections import defaultdict, namedtuple
import copy

In [0]:
from mnist_m import Mnist_M
from datasets_merge import Merge_Datasets
import models
import trainer
import domain_trainer
from test_model import test_model
import plots
import test
import plotly_plots

In [0]:
def convertMnist(img):
  img = img.squeeze().numpy()
  return torch.from_numpy(np.tile(img, (3,1,1)))

In [0]:
batch_size=128
num_workers=1

In [11]:
transform=transforms.Compose([
                           transforms.ToTensor(),
                           transforms.Normalize((0.1307,), (0.3081,)),
                           transforms.Lambda(convertMnist)
                       ])

train_set = torchvision.datasets.MNIST(root='./data', train=True, download=True,
                                     transform=transform)
train_loader = torch.utils.data.DataLoader(train_set, batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)

test_set = torchvision.datasets.MNIST(root='./data', train=False, download=True,
                                     transform=transform)
test_loader = torch.utils.data.DataLoader(test_set, batch_size=batch_size,
                                         shuffle=False, num_workers=num_workers)




Processing...
Done!


In [0]:
log_interval = 100

In [0]:
use_cuda = True
use_cuda = use_cuda and torch.cuda.is_available()
device = torch.device("cuda" if use_cuda else "cpu")

In [0]:
lr = 0.01
momentum=0.9

In [0]:
mnist_m_transform = transforms.Compose([
                           transforms.Normalize(3*[0.1307], 3*[0.3081]),
                       ])
mnist_m_train = Mnist_M('drive/My Drive/BScThesis/keras_mnistm.pkl',
                        transform=mnist_m_transform)
mnist_m_test = Mnist_M('drive/My Drive/BScThesis/keras_mnistm.pkl',train=False,
                     transform=mnist_m_transform)
mnist_m_train_loader = torch.utils.data.DataLoader(mnist_m_train, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)
mnist_m_test_loader = torch.utils.data.DataLoader(mnist_m_test,
                                                  batch_size=batch_size,
                                         shuffle=False, num_workers=num_workers)




In [0]:
Models = namedtuple('Models', ['model_f', 'model_c', 'model_d'])
Optims = namedtuple('Optims', ['optim_f', 'optim_c', 'optim_d'])
Criterions = namedtuple('Criterions', ['criterion', 'criterion_domain'])
Loaders = namedtuple('Loaders', ['train_loader', 'train_loader_domain',
                                'source_test_loader', 'target_test_loader',
                                'merged_test_loader'])

In [0]:
mnist_ext_train = Merge_Datasets([train_set, mnist_m_train])
mnist_ext_test = Merge_Datasets([test_set, mnist_m_test])
mnist_ext_train_loader = torch.utils.data.DataLoader(mnist_ext_train, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)
mnist_ext_test_loader = torch.utils.data.DataLoader(mnist_ext_test, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)





In [0]:
loaders = Loaders(train_loader, mnist_m_train_loader,
                 test_loader, mnist_m_test_loader, mnist_ext_test_loader)

In [0]:
criterion = F.nll_loss
criterion_domain = F.nll_loss

In [0]:
criterions = Criterions(criterion, criterion_domain)

In [0]:
epochs=8

In [0]:
model_f_3_layer = nn.Sequential(nn.Linear(320,3))
model_f = models.extend_feature_extractor(models.MnistFeatureExtractor(), 
                                         model_f_3_layer, False, False).to(device)
model_c = models.MnistClassPredictor(input_size=3).to(device)
model_d = models.MnistDomain(input_size=3).to(device)


In [0]:
optim_f = optim.SGD(model_f.parameters(), lr=lr, momentum=momentum, nesterov=True)
optim_c = optim.SGD(model_c.parameters(), lr=lr, momentum=momentum, nesterov=True)
optim_d = optim.SGD(model_d.parameters(), lr=lr, momentum=momentum, nesterov=True)

In [0]:
train_models = Models(model_f, model_c, model_d)
optims = Optims(optim_f, optim_c, optim_d)

In [0]:
model_trainer = trainer.Trainer(train_models, optims, criterions, device,
                                train_domain=False, tune_lr=True)

In [68]:
test_history = defaultdict(lambda:[])
model_trainer.train(epochs, loaders, test_history=test_history)

Train Epoch: 					1 [0/60000 (0%)]	Loss: 2.351116, lr: 0.01000 lambd: 1.00000
Train Epoch: 					1 [12800/60000 (21%)]	Loss: 0.895067, lr: 0.00838 lambd: 1.00000
Train Epoch: 					1 [25600/60000 (43%)]	Loss: 0.575942, lr: 0.00726 lambd: 1.00000
Train Epoch: 					1 [38400/60000 (64%)]	Loss: 0.471056, lr: 0.00643 lambd: 1.00000
Train Epoch: 					1 [51200/60000 (85%)]	Loss: 0.310744, lr: 0.00580 lambd: 1.00000

Target Domain Test set: Average loss: 1.9956, Accuracy: 3033/10000 (30%)
Source Domain Test set: Average loss: 0.1833, Accuracy: 9433/10000 (94%)
Domains predictor:  Accuracy: 10484/20000 (52%)

Train Epoch: 					2 [0/60000 (0%)]	Loss: 0.269672, lr: 0.00544 lambd: 1.00000
Train Epoch: 					2 [12800/60000 (21%)]	Loss: 0.277167, lr: 0.00500 lambd: 1.00000
Train Epoch: 					2 [25600/60000 (43%)]	Loss: 0.297240, lr: 0.00464 lambd: 1.00000
Train Epoch: 					2 [38400/60000 (64%)]	Loss: 0.250886, lr: 0.00433 lambd: 1.00000
Train Epoch: 					2 [51200/60000 (85%)]	Loss: 0.530862, lr: 0.00407

In [0]:
def get_input_mtx(loader, model, c_size):
  X = np.zeros(c_size).T
  for batch_idx, (data, labels) in enumerate(loader):
    data = data.to(device)
    idx = batch_idx * loader.batch_size
    X[idx:idx+loader.batch_size] = model(data).cpu().detach().numpy()
  return X.T

In [0]:
X = get_input_mtx(test_loader, model_f, (3, len(test_set)))

In [0]:
X_m = get_input_mtx(mnist_m_test_loader, model_f, (3, len(mnist_m_test)))

In [0]:
def get_conceptor(X, alpha):
  R = np.matmul(X, X.T) * (1/X.shape[0])
  IdX = np.identity(X.shape[0])
  return np.matmul(R, np.linalg.inv((R + alpha**(-2) * IdX)))

In [0]:
def quota(C):
  U, S, U_T = np.linalg.svd(C)
  return np.sum(S) / len(S)

In [0]:
def get_by_label(dataset, label_set, label):
  res = []
  for i, data in enumerate(label_set):
    if data[1] == label:
      res.append(dataset[i])
  return res

In [0]:
X_0 = get_by_label(X.T, test_set, 0)

In [0]:
X_0 = np.array(X_0).T

In [0]:
X_m_0 = get_by_label(X_m.T, mnist_m_test, 0)

In [0]:
X_m_0 = np.array(X_m_0).T

In [0]:
C = get_conceptor(X, 0.01)

In [59]:
quota(C)

0.17697276493679012

In [60]:
C

array([[ 0.17344993, -0.03240449,  0.01556786],
       [-0.03240449,  0.16936567,  0.01324563],
       [ 0.01556786,  0.01324563,  0.1881027 ]])

In [61]:
np.linalg.eig(C)

(array([0.13162431, 0.20439787, 0.19489612]),
 array([[-0.65178795, -0.75619635,  0.05778881],
        [-0.67852248,  0.61548199,  0.40098525],
        [ 0.33879156, -0.22214635,  0.91425996]]))

In [0]:
import plotly
from plotly import tools
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objs as go

# Plot for model with leaky ReLU

In [76]:
[x,y,z] = X
trace1 = go.Scatter3d(x=x,y=y,z=z, mode='markers', marker=dict(
        size=12,line=dict(color='rgba(217, 217, 217, 0.14)',width=0.5),opacity=0.8))

[x2, y2, z2] = X_m
trace2 = go.Scatter3d(x=x2,y=y2,z=z2,mode='markers',marker=dict(
        color='rgb(127, 127, 127)',size=12,symbol='circle',line=dict(color='rgb(204, 204, 204)',width=1),opacity=0.9))

[x3, y3, z3] = X_0
trace3 = go.Scatter3d(x=x3,y=y3,z=z3,mode='markers',marker=dict(color='rgb(255, 255, 204)',
        size=12,symbol='circle',line=dict(color='rgb(255, 255, 20)',width=1),opacity=0.9))

[x4, y4, z4] = X_m_0
trace4 = go.Scatter3d(x=x4,y=y4,z=z4,mode='markers',marker=dict(color='rgb(0, 255, 204)',
        size=12,symbol='circle',line=dict(color='rgb(0, 255, 20)',width=1),opacity=0.9))

data = [trace1, trace2, trace3, trace4]
layout = go.Layout(margin=dict(l=0,r=0,b=0,t=0))
fig = go.Figure(data=data, layout=layout)

plotly_plots.configure_plotly_browser_state()

init_notebook_mode(connected=False)

fig['layout'].update(height=800, width=1200, title='MNIST')
plotly.offline.iplot(fig, filename='basic-line')

# Plot for model with two tanh layers

In [63]:
[x,y,z] = X
trace1 = go.Scatter3d(x=x,y=y,z=z, mode='markers', marker=dict(
        size=12,line=dict(color='rgba(217, 217, 217, 0.14)',width=0.5),opacity=0.8))

[x2, y2, z2] = X_m
trace2 = go.Scatter3d(x=x2,y=y2,z=z2,mode='markers',marker=dict(
        color='rgb(127, 127, 127)',size=12,symbol='circle',line=dict(color='rgb(204, 204, 204)',width=1),opacity=0.9))

[x3, y3, z3] = X_0
trace3 = go.Scatter3d(x=x3,y=y3,z=z3,mode='markers',marker=dict(color='rgb(255, 255, 204)',
        size=12,symbol='circle',line=dict(color='rgb(255, 255, 20)',width=1),opacity=0.9))

[x4, y4, z4] = X_m_0
trace4 = go.Scatter3d(x=x4,y=y4,z=z4,mode='markers',marker=dict(color='rgb(0, 255, 204)',
        size=12,symbol='circle',line=dict(color='rgb(0, 255, 20)',width=1),opacity=0.9))

data = [trace1, trace2, trace3, trace4]
layout = go.Layout(margin=dict(l=0,r=0,b=0,t=0))
fig = go.Figure(data=data, layout=layout)

plotly_plots.configure_plotly_browser_state()

init_notebook_mode(connected=False)

fig['layout'].update(height=800, width=1200, title='MNIST')
plotly.offline.iplot(fig, filename='basic-line')